In [94]:
import numpy as np
import matplotlib.pyplot as plt
from matplotlib.pyplot import figure
import pandas as pd

from sklearn.model_selection import train_test_split
from sklearn.model_selection import cross_val_score
from sklearn.model_selection import ShuffleSplit
from sklearn.model_selection import GridSearchCV


from sklearn.utils import resample


## Setup

In [95]:
# load data
data = pd.read_csv('../../data/ml_input.csv')

# set index
data = data.set_index('pairs')

# downsample non-infection data
noninf_messages = data[data['infection']=='NoInf']
inf_messages = data[data['infection']=='Inf']
ntarget_samples = int(len(inf_messages) + 0.50 * len(inf_messages))
noninf_downsample = resample(noninf_messages, replace=True, n_samples=ntarget_samples)
tmp = pd.concat([noninf_downsample, inf_messages])

# select relevant rows for machine learning model 
ml_input = tmp[['GCdiff', 'k3dist', 'k6dist', 'Homology']]
print('The dataframe is made of {} rows and {} columns!'.format(ml_input.shape[0], ml_input.shape[1]))
ml_input.head()

bootstrap = 50

The dataframe is made of 6925 rows and 4 columns!


In [96]:
# retrieve target
ml_target = tmp['infection']

# replace categorical values with numbers
ml_target = ml_target.map({'NoInf' : 0, 'Inf': 1})
ml_target.head()

ml_target.value_counts()[0] / (ml_target.value_counts()[0] + ml_target.value_counts()[1]) 

0.6

In [97]:
X_train, X_test, y_train, y_test = train_test_split(ml_input, ml_target, 
                                                    shuffle=True, random_state = 5, 
                                                    test_size = 0.3, train_size = 0.7)


In [98]:
shuffle_split = ShuffleSplit(test_size = 0.3, train_size = 0.7, n_splits = 10)

List to store the results of the grid search

In [99]:
model_name = []
best_score = []

## Support vector machines

In [100]:
from sklearn import svm

In [101]:
model = svm.SVC()
model.fit(X_train, y_train)

print("Accuracy on training set: {:.3f}".format(model.score(X_train, y_train)))
print("Accuracy on test set: {:.3f}".format(model.score(X_test, y_test)))


Accuracy on training set: 0.745
Accuracy on test set: 0.743


In [102]:
shuffle_split = ShuffleSplit(test_size = 0.3, train_size = 0.7, n_splits = 10)
scores = cross_val_score(model, ml_input, ml_target, cv = shuffle_split)
print("Cross_validation scores:\n{}".format(scores))
print("Average cross-validation score: {:.3f}".format(scores.mean()))

Cross_validation scores:
[0.74687199 0.75986526 0.73965351 0.74927815 0.73147257 0.74109721
 0.71799808 0.7574591  0.7666025  0.74157844]
Average cross-validation score: 0.745


### Grid search

In [103]:
param_grid = {'C': [0.1,1, 10, 100], 
              'gamma': [1,0.1,0.01,0.001],
              'kernel': ['rbf', 'poly', 'sigmoid']}

In [104]:
grid_search = GridSearchCV(svm.SVC(), param_grid, cv=ShuffleSplit(), n_jobs=7, return_train_score=True)


In [105]:
train_size = 0.7
test_size = 1 - train_size

ROC_disp = None
F1_disp = None

noninf_messages = data[data['infection']=='NoInf']
inf_messages = data[data['infection']=='Inf']

for i in range(0, 1):
    print(f'bootstrap number {i}')

    # fix imbalance
    noninf_downsample = resample(noninf_messages, replace=True, n_samples=ntarget_samples)
    boot_data = pd.concat([noninf_downsample, inf_messages])
    print(boot_data['infection'].value_counts())

    # prep input data
    ml_data = boot_data[['GCdiff', 'k3dist', 'k6dist', 'Homology']]
    ml_target = boot_data['infection']
    ml_target = ml_target.map({'NoInf' : 0, 'Inf': 1})

    # split data
    X_train, X_test, y_train, y_test = train_test_split(ml_data, ml_target, random_state=0, test_size=test_size, train_size=train_size)
    
    # grid search
    grid_search.fit(X_train, y_train)

    print("Test set score: {:.2f}".format(grid_search.score(X_test, y_test)))
    print("Best parameters: {}".format(grid_search.best_params_))
    print("Best cross-validation score: {:.2f}".format(grid_search.best_score_))
    print("Best estimator:\n{}".format(grid_search.best_estimator_))

    model_name.append('SVM')
    best_score.append(grid_search.score(X_test, y_test))



bootstrap number 0
NoInf    4155
Inf      2770
Name: infection, dtype: int64
Test set score: 0.79
Best parameters: {'C': 100, 'gamma': 1, 'kernel': 'rbf'}
Best cross-validation score: 0.79
Best estimator:
SVC(C=100, gamma=1)


## Stochastic gradient descent

In [106]:
from sklearn.linear_model import SGDClassifier

In [107]:
model = SGDClassifier(loss="hinge", penalty="l2", max_iter=100)
model.fit(X_train, y_train)

print("Accuracy on training set: {:.3f}".format(model.score(X_train, y_train)))
print("Accuracy on test set: {:.3f}".format(model.score(X_test, y_test)))


Accuracy on training set: 0.702
Accuracy on test set: 0.705


In [108]:
shuffle_split = ShuffleSplit(test_size = 0.3, train_size = 0.7, n_splits = 10)
scores = cross_val_score(model, ml_input, ml_target, cv = shuffle_split)
print("Cross_validation scores:\n{}".format(scores))
print("Average cross-validation score: {:.3f}".format(scores.mean()))

Cross_validation scores:
[0.73435996 0.74975938 0.71318576 0.73051011 0.75505294 0.72617902
 0.75697786 0.73099134 0.71703561 0.72906641]
Average cross-validation score: 0.734


### Grid search

In [109]:
param_grid = {'loss': ['hinge', 'modified_huber', 'log_loss', 'squared_hinge', 'perceptron', 'squared_error', 'huber', 'epsilon_insensitive'],
              'penalty': ['l2', 'l1', 'elasticnet', None],
              'alpha': [0.0001, 0.001, 0.01], 
              'max_iter': [500]}

In [110]:
grid_search = GridSearchCV(SGDClassifier(), param_grid, cv=ShuffleSplit(), n_jobs=7, return_train_score=True)


In [111]:
train_size = 0.7
test_size = 1 - train_size

ROC_disp = None
F1_disp = None

noninf_messages = data[data['infection']=='NoInf']
inf_messages = data[data['infection']=='Inf']

for i in range(0, bootstrap):
    print(f'bootstrap number {i}')

    # fix imbalance
    noninf_downsample = resample(noninf_messages, replace=True, n_samples=ntarget_samples)
    boot_data = pd.concat([noninf_downsample, inf_messages])
    print(boot_data['infection'].value_counts())

    # prep input data
    ml_data = boot_data[['GCdiff', 'k3dist', 'k6dist', 'Homology']]
    ml_target = boot_data['infection']
    ml_target = ml_target.map({'NoInf' : 0, 'Inf': 1})

    # split data
    X_train, X_test, y_train, y_test = train_test_split(ml_data, ml_target, random_state=0, test_size=test_size, train_size=train_size)
    
    # grid search
    grid_search.fit(X_train, y_train)

    print("Test set score: {:.2f}".format(grid_search.score(X_test, y_test)))
    print("Best parameters: {}".format(grid_search.best_params_))
    print("Best cross-validation score: {:.2f}".format(grid_search.best_score_))
    print("Best estimator:\n{}".format(grid_search.best_estimator_))

    model_name.append('StochasticDescentGradient')
    best_score.append(grid_search.score(X_test, y_test))


bootstrap number 0
NoInf    4155
Inf      2770
Name: infection, dtype: int64


/Users/gbastien/opt/anaconda3/envs/vip/lib/python3.10/site-packages/sklearn/linear_model/_stochastic_gradient.py:702: ConvergenceWarning: Maximum number of iteration reached before convergence. Consider increasing max_iter to improve the fit.
  warnings.warn(
/Users/gbastien/opt/anaconda3/envs/vip/lib/python3.10/site-packages/sklearn/linear_model/_stochastic_gradient.py:702: ConvergenceWarning: Maximum number of iteration reached before convergence. Consider increasing max_iter to improve the fit.
  warnings.warn(
/Users/gbastien/opt/anaconda3/envs/vip/lib/python3.10/site-packages/sklearn/linear_model/_stochastic_gradient.py:702: ConvergenceWarning: Maximum number of iteration reached before convergence. Consider increasing max_iter to improve the fit.
  warnings.warn(
/Users/gbastien/opt/anaconda3/envs/vip/lib/python3.10/site-packages/sklearn/linear_model/_stochastic_gradient.py:702: ConvergenceWarning: Maximum number of iteration reached before convergence. Consider increasing max_it

Test set score: 0.70
Best parameters: {'alpha': 0.001, 'loss': 'modified_huber', 'max_iter': 500, 'penalty': None}
Best cross-validation score: 0.73
Best estimator:
SGDClassifier(alpha=0.001, loss='modified_huber', max_iter=500, penalty=None)
bootstrap number 1
NoInf    4155
Inf      2770
Name: infection, dtype: int64


/Users/gbastien/opt/anaconda3/envs/vip/lib/python3.10/site-packages/sklearn/linear_model/_stochastic_gradient.py:702: ConvergenceWarning: Maximum number of iteration reached before convergence. Consider increasing max_iter to improve the fit.
  warnings.warn(
/Users/gbastien/opt/anaconda3/envs/vip/lib/python3.10/site-packages/sklearn/linear_model/_stochastic_gradient.py:702: ConvergenceWarning: Maximum number of iteration reached before convergence. Consider increasing max_iter to improve the fit.
  warnings.warn(
/Users/gbastien/opt/anaconda3/envs/vip/lib/python3.10/site-packages/sklearn/linear_model/_stochastic_gradient.py:702: ConvergenceWarning: Maximum number of iteration reached before convergence. Consider increasing max_iter to improve the fit.
  warnings.warn(
/Users/gbastien/opt/anaconda3/envs/vip/lib/python3.10/site-packages/sklearn/linear_model/_stochastic_gradient.py:702: ConvergenceWarning: Maximum number of iteration reached before convergence. Consider increasing max_it

Test set score: 0.74
Best parameters: {'alpha': 0.001, 'loss': 'modified_huber', 'max_iter': 500, 'penalty': None}
Best cross-validation score: 0.74
Best estimator:
SGDClassifier(alpha=0.001, loss='modified_huber', max_iter=500, penalty=None)
bootstrap number 2
NoInf    4155
Inf      2770
Name: infection, dtype: int64


...

/Users/gbastien/opt/anaconda3/envs/vip/lib/python3.10/site-packages/sklearn/linear_model/_stochastic_gradient.py:702: ConvergenceWarning: Maximum number of iteration reached before convergence. Consider increasing max_iter to improve the fit.
  warnings.warn(
/Users/gbastien/opt/anaconda3/envs/vip/lib/python3.10/site-packages/sklearn/linear_model/_stochastic_gradient.py:702: ConvergenceWarning: Maximum number of iteration reached before convergence. Consider increasing max_iter to improve the fit.
  warnings.warn(
/Users/gbastien/opt/anaconda3/envs/vip/lib/python3.10/site-packages/sklearn/linear_model/_stochastic_gradient.py:702: ConvergenceWarning: Maximum number of iteration reached before convergence. Consider increasing max_iter to improve the fit.
  warnings.warn(
/Users/gbastien/opt/anaconda3/envs/vip/lib/python3.10/site-packages/sklearn/linear_model/_stochastic_gradient.py:702: ConvergenceWarning: Maximum number of iteration reached before convergence. Consider increasing max_it

Test set score: 0.74
Best parameters: {'alpha': 0.01, 'loss': 'log_loss', 'max_iter': 500, 'penalty': 'l2'}
Best cross-validation score: 0.72
Best estimator:
SGDClassifier(alpha=0.01, loss='log_loss', max_iter=500)
bootstrap number 49
NoInf    4155
Inf      2770
Name: infection, dtype: int64


/Users/gbastien/opt/anaconda3/envs/vip/lib/python3.10/site-packages/sklearn/linear_model/_stochastic_gradient.py:702: ConvergenceWarning: Maximum number of iteration reached before convergence. Consider increasing max_iter to improve the fit.
  warnings.warn(
/Users/gbastien/opt/anaconda3/envs/vip/lib/python3.10/site-packages/sklearn/linear_model/_stochastic_gradient.py:702: ConvergenceWarning: Maximum number of iteration reached before convergence. Consider increasing max_iter to improve the fit.
  warnings.warn(
/Users/gbastien/opt/anaconda3/envs/vip/lib/python3.10/site-packages/sklearn/linear_model/_stochastic_gradient.py:702: ConvergenceWarning: Maximum number of iteration reached before convergence. Consider increasing max_iter to improve the fit.
  warnings.warn(
/Users/gbastien/opt/anaconda3/envs/vip/lib/python3.10/site-packages/sklearn/linear_model/_stochastic_gradient.py:702: ConvergenceWarning: Maximum number of iteration reached before convergence. Consider increasing max_it

Test set score: 0.75
Best parameters: {'alpha': 0.01, 'loss': 'log_loss', 'max_iter': 500, 'penalty': 'l1'}
Best cross-validation score: 0.73
Best estimator:
SGDClassifier(alpha=0.01, loss='log_loss', max_iter=500, penalty='l1')


/Users/gbastien/opt/anaconda3/envs/vip/lib/python3.10/site-packages/sklearn/linear_model/_stochastic_gradient.py:702: ConvergenceWarning: Maximum number of iteration reached before convergence. Consider increasing max_iter to improve the fit.
  warnings.warn(
/Users/gbastien/opt/anaconda3/envs/vip/lib/python3.10/site-packages/sklearn/linear_model/_stochastic_gradient.py:702: ConvergenceWarning: Maximum number of iteration reached before convergence. Consider increasing max_iter to improve the fit.
  warnings.warn(
/Users/gbastien/opt/anaconda3/envs/vip/lib/python3.10/site-packages/sklearn/linear_model/_stochastic_gradient.py:702: ConvergenceWarning: Maximum number of iteration reached before convergence. Consider increasing max_iter to improve the fit.
  warnings.warn(
/Users/gbastien/opt/anaconda3/envs/vip/lib/python3.10/site-packages/sklearn/linear_model/_stochastic_gradient.py:702: ConvergenceWarning: Maximum number of iteration reached before convergence. Consider increasing max_it

## K Neighbors Classifier

In [112]:
from sklearn.neighbors import KNeighborsClassifier

In [113]:
model = KNeighborsClassifier()
model.fit(X_train, y_train)

print("Accuracy on training set: {:.3f}".format(model.score(X_train, y_train)))
print("Accuracy on test set: {:.3f}".format(model.score(X_test, y_test)))


Accuracy on training set: 0.860
Accuracy on test set: 0.792


In [114]:
shuffle_split = ShuffleSplit(test_size = 0.3, train_size = 0.7, n_splits = 10)
scores = cross_val_score(model, ml_input, ml_target, cv = shuffle_split)
print("Cross_validation scores:\n{}".format(scores))
print("Average cross-validation score: {:.3f}".format(scores.mean()))

Cross_validation scores:
[0.80991338 0.81809432 0.81905679 0.8147257  0.80365736 0.80558229
 0.80558229 0.81424447 0.81231954 0.81087584]
Average cross-validation score: 0.811


### Grid search

In [115]:
param_grid = {'n_neighbors': (1, 5, 10, 15),
                  'leaf_size': (1, 20, 40, 100, 150),
                  'p': (1, 2),
                  'weights': ('uniform', 'distance'),
                  'metric': ('minkowski', 'chebyshev')}

In [116]:
grid_search = GridSearchCV(KNeighborsClassifier(), param_grid, cv=ShuffleSplit(), n_jobs=7, return_train_score=True)


In [117]:
train_size = 0.7
test_size = 1 - train_size

ROC_disp = None
F1_disp = None

noninf_messages = data[data['infection']=='NoInf']
inf_messages = data[data['infection']=='Inf']

for i in range(0, bootstrap):
    print(f'bootstrap number {i}')

    # fix imbalance
    noninf_downsample = resample(noninf_messages, replace=True, n_samples=ntarget_samples)
    boot_data = pd.concat([noninf_downsample, inf_messages])
    print(boot_data['infection'].value_counts())

    # prep input data
    ml_data = boot_data[['GCdiff', 'k3dist', 'k6dist', 'Homology']]
    ml_target = boot_data['infection']
    ml_target = ml_target.map({'NoInf' : 0, 'Inf': 1})

    # split data
    X_train, X_test, y_train, y_test = train_test_split(ml_data, ml_target, random_state=0, test_size=test_size, train_size=train_size)
    
    # grid search
    grid_search.fit(X_train, y_train)

    print("Test set score: {:.2f}".format(grid_search.score(X_test, y_test)))
    print("Best parameters: {}".format(grid_search.best_params_))
    print("Best cross-validation score: {:.2f}".format(grid_search.best_score_))
    print("Best estimator:\n{}".format(grid_search.best_estimator_))

    model_name.append('KNeighborsClassifier')
    best_score.append(grid_search.score(X_test, y_test))


bootstrap number 0
NoInf    4155
Inf      2770
Name: infection, dtype: int64
Test set score: 0.85
Best parameters: {'leaf_size': 1, 'metric': 'minkowski', 'n_neighbors': 5, 'p': 1, 'weights': 'distance'}
Best cross-validation score: 0.84
Best estimator:
KNeighborsClassifier(leaf_size=1, p=1, weights='distance')
bootstrap number 1
NoInf    4155
Inf      2770
Name: infection, dtype: int64
Test set score: 0.84
Best parameters: {'leaf_size': 1, 'metric': 'minkowski', 'n_neighbors': 15, 'p': 1, 'weights': 'distance'}
Best cross-validation score: 0.85
Best estimator:
KNeighborsClassifier(leaf_size=1, n_neighbors=15, p=1, weights='distance')
bootstrap number 2
NoInf    4155
Inf      2770
Name: infection, dtype: int64
Test set score: 0.85
Best parameters: {'leaf_size': 1, 'metric': 'minkowski', 'n_neighbors': 10, 'p': 1, 'weights': 'distance'}
Best cross-validation score: 0.84
Best estimator:
KNeighborsClassifier(leaf_size=1, n_neighbors=10, p=1, weights='distance')
bootstrap number 3
NoInf   

## Gaussian Process Classifier



In [118]:
from sklearn.gaussian_process import GaussianProcessClassifier
from sklearn.gaussian_process.kernels import RBF

In [119]:
kernel = 1.0 * RBF(1.0)
model = GaussianProcessClassifier(kernel=kernel)
model.fit(X_train, y_train)

print("Accuracy on training set: {:.3f}".format(model.score(X_train, y_train)))
print("Accuracy on test set: {:.3f}".format(model.score(X_test, y_test)))


Accuracy on training set: 0.901
Accuracy on test set: 0.828


## Random Forest



In [120]:
from sklearn.ensemble import RandomForestClassifier

In [121]:
model = RandomForestClassifier()
model.fit(X_train, y_train)

print("Accuracy on training set: {:.3f}".format(model.score(X_train, y_train)))
print("Accuracy on test set: {:.3f}".format(model.score(X_test, y_test)))


Accuracy on training set: 1.000
Accuracy on test set: 0.888


### Grid search

In [122]:
param_grid = { 
    'n_estimators': [200, 500],
    'max_features': ['auto', 'sqrt', 'log2'],
    'max_depth' : [4,5,6,7,8,9,10,15,20],
    'criterion' :['gini', 'entropy']
}

In [123]:
grid_search = GridSearchCV(RandomForestClassifier(), param_grid, cv=ShuffleSplit(), n_jobs=7, return_train_score=True)


In [124]:
train_size = 0.7
test_size = 1 - train_size

ROC_disp = None
F1_disp = None

noninf_messages = data[data['infection']=='NoInf']
inf_messages = data[data['infection']=='Inf']

for i in range(0, bootstrap):
    print(f'bootstrap number {i}')

    # fix imbalance
    noninf_downsample = resample(noninf_messages, replace=True, n_samples=ntarget_samples)
    boot_data = pd.concat([noninf_downsample, inf_messages])
    print(boot_data['infection'].value_counts())

    # prep input data
    ml_data = boot_data[['GCdiff', 'k3dist', 'k6dist', 'Homology']]
    ml_target = boot_data['infection']
    ml_target = ml_target.map({'NoInf' : 0, 'Inf': 1})

    # split data
    X_train, X_test, y_train, y_test = train_test_split(ml_data, ml_target, random_state=0, test_size=test_size, train_size=train_size)
    
    # grid search
    grid_search.fit(X_train, y_train)

    print("Test set score: {:.2f}".format(grid_search.score(X_test, y_test)))
    print("Best parameters: {}".format(grid_search.best_params_))
    print("Best cross-validation score: {:.2f}".format(grid_search.best_score_))
    print("Best estimator:\n{}".format(grid_search.best_estimator_))

    model_name.append('RandomForest')
    best_score.append(grid_search.score(X_test, y_test))
    


bootstrap number 0
NoInf    4155
Inf      2770
Name: infection, dtype: int64


/Users/gbastien/opt/anaconda3/envs/vip/lib/python3.10/site-packages/sklearn/ensemble/_forest.py:424: FutureWarning: `max_features='auto'` has been deprecated in 1.1 and will be removed in 1.3. To keep the past behaviour, explicitly set `max_features='sqrt'` or remove this parameter as it is also the default value for RandomForestClassifiers and ExtraTreesClassifiers.
  warn(
/Users/gbastien/opt/anaconda3/envs/vip/lib/python3.10/site-packages/sklearn/ensemble/_forest.py:424: FutureWarning: `max_features='auto'` has been deprecated in 1.1 and will be removed in 1.3. To keep the past behaviour, explicitly set `max_features='sqrt'` or remove this parameter as it is also the default value for RandomForestClassifiers and ExtraTreesClassifiers.
  warn(
/Users/gbastien/opt/anaconda3/envs/vip/lib/python3.10/site-packages/sklearn/ensemble/_forest.py:424: FutureWarning: `max_features='auto'` has been deprecated in 1.1 and will be removed in 1.3. To keep the past behaviour, explicitly set `max_fea

Test set score: 0.89
Best parameters: {'criterion': 'entropy', 'max_depth': 20, 'max_features': 'log2', 'n_estimators': 200}
Best cross-validation score: 0.87
Best estimator:
RandomForestClassifier(criterion='entropy', max_depth=20, max_features='log2',
                       n_estimators=200)
bootstrap number 1
NoInf    4155
Inf      2770
Name: infection, dtype: int64


/Users/gbastien/opt/anaconda3/envs/vip/lib/python3.10/site-packages/sklearn/ensemble/_forest.py:424: FutureWarning: `max_features='auto'` has been deprecated in 1.1 and will be removed in 1.3. To keep the past behaviour, explicitly set `max_features='sqrt'` or remove this parameter as it is also the default value for RandomForestClassifiers and ExtraTreesClassifiers.
  warn(
/Users/gbastien/opt/anaconda3/envs/vip/lib/python3.10/site-packages/sklearn/ensemble/_forest.py:424: FutureWarning: `max_features='auto'` has been deprecated in 1.1 and will be removed in 1.3. To keep the past behaviour, explicitly set `max_features='sqrt'` or remove this parameter as it is also the default value for RandomForestClassifiers and ExtraTreesClassifiers.
  warn(
/Users/gbastien/opt/anaconda3/envs/vip/lib/python3.10/site-packages/sklearn/ensemble/_forest.py:424: FutureWarning: `max_features='auto'` has been deprecated in 1.1 and will be removed in 1.3. To keep the past behaviour, explicitly set `max_fea

Test set score: 0.89
Best parameters: {'criterion': 'gini', 'max_depth': 20, 'max_features': 'sqrt', 'n_estimators': 500}
Best cross-validation score: 0.88
Best estimator:
RandomForestClassifier(max_depth=20, n_estimators=500)
bootstrap number 2
NoInf    4155
Inf      2770
Name: infection, dtype: int64


...

Test set score: 0.88
Best parameters: {'criterion': 'gini', 'max_depth': 20, 'max_features': 'sqrt', 'n_estimators': 200}
Best cross-validation score: 0.89
Best estimator:
RandomForestClassifier(max_depth=20, n_estimators=200)
bootstrap number 48
NoInf    4155
Inf      2770
Name: infection, dtype: int64


/Users/gbastien/opt/anaconda3/envs/vip/lib/python3.10/site-packages/sklearn/ensemble/_forest.py:424: FutureWarning: `max_features='auto'` has been deprecated in 1.1 and will be removed in 1.3. To keep the past behaviour, explicitly set `max_features='sqrt'` or remove this parameter as it is also the default value for RandomForestClassifiers and ExtraTreesClassifiers.
  warn(
/Users/gbastien/opt/anaconda3/envs/vip/lib/python3.10/site-packages/sklearn/ensemble/_forest.py:424: FutureWarning: `max_features='auto'` has been deprecated in 1.1 and will be removed in 1.3. To keep the past behaviour, explicitly set `max_features='sqrt'` or remove this parameter as it is also the default value for RandomForestClassifiers and ExtraTreesClassifiers.
  warn(
/Users/gbastien/opt/anaconda3/envs/vip/lib/python3.10/site-packages/sklearn/ensemble/_forest.py:424: FutureWarning: `max_features='auto'` has been deprecated in 1.1 and will be removed in 1.3. To keep the past behaviour, explicitly set `max_fea

Test set score: 0.88
Best parameters: {'criterion': 'gini', 'max_depth': 20, 'max_features': 'auto', 'n_estimators': 500}
Best cross-validation score: 0.89
Best estimator:
RandomForestClassifier(max_depth=20, max_features='auto', n_estimators=500)
bootstrap number 49
NoInf    4155
Inf      2770
Name: infection, dtype: int64


/Users/gbastien/opt/anaconda3/envs/vip/lib/python3.10/site-packages/sklearn/ensemble/_forest.py:424: FutureWarning: `max_features='auto'` has been deprecated in 1.1 and will be removed in 1.3. To keep the past behaviour, explicitly set `max_features='sqrt'` or remove this parameter as it is also the default value for RandomForestClassifiers and ExtraTreesClassifiers.
  warn(
/Users/gbastien/opt/anaconda3/envs/vip/lib/python3.10/site-packages/sklearn/ensemble/_forest.py:424: FutureWarning: `max_features='auto'` has been deprecated in 1.1 and will be removed in 1.3. To keep the past behaviour, explicitly set `max_features='sqrt'` or remove this parameter as it is also the default value for RandomForestClassifiers and ExtraTreesClassifiers.
  warn(
/Users/gbastien/opt/anaconda3/envs/vip/lib/python3.10/site-packages/sklearn/ensemble/_forest.py:424: FutureWarning: `max_features='auto'` has been deprecated in 1.1 and will be removed in 1.3. To keep the past behaviour, explicitly set `max_fea

Test set score: 0.88
Best parameters: {'criterion': 'gini', 'max_depth': 20, 'max_features': 'sqrt', 'n_estimators': 500}
Best cross-validation score: 0.89
Best estimator:
RandomForestClassifier(max_depth=20, n_estimators=500)


In [125]:
print(model_name)
print(best_score)
bootstrap

['SVM', 'StochasticDescentGradient', 'StochasticDescentGradient', 'StochasticDescentGradient', 'StochasticDescentGradient', 'StochasticDescentGradient', 'StochasticDescentGradient', 'StochasticDescentGradient', 'StochasticDescentGradient', 'StochasticDescentGradient', 'StochasticDescentGradient', 'StochasticDescentGradient', 'StochasticDescentGradient', 'StochasticDescentGradient', 'StochasticDescentGradient', 'StochasticDescentGradient', 'StochasticDescentGradient', 'StochasticDescentGradient', 'StochasticDescentGradient', 'StochasticDescentGradient', 'StochasticDescentGradient', 'StochasticDescentGradient', 'StochasticDescentGradient', 'StochasticDescentGradient', 'StochasticDescentGradient', 'StochasticDescentGradient', 'StochasticDescentGradient', 'StochasticDescentGradient', 'StochasticDescentGradient', 'StochasticDescentGradient', 'StochasticDescentGradient', 'StochasticDescentGradient', 'StochasticDescentGradient', 'StochasticDescentGradient', 'StochasticDescentGradient', 'Stoch

50

In [126]:
for i in range(0, bootstrap):
    print(i)

0
1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49


## Ada Boost 

In [127]:
from sklearn.ensemble import AdaBoostClassifier

In [128]:
model = AdaBoostClassifier()
model.fit(X_train, y_train)

print("Accuracy on training set: {:.3f}".format(model.score(X_train, y_train)))
print("Accuracy on test set: {:.3f}".format(model.score(X_test, y_test)))


Accuracy on training set: 0.789
Accuracy on test set: 0.764


### Grid search

In [129]:

param_grid = {"n_estimators": [1, 2, 3, 4, 5, 10, 15],
                "learning_rate": [0.001, 0.01, 0.1, 1, 2]
             }

In [130]:
grid_search = GridSearchCV(AdaBoostClassifier(), param_grid, cv=ShuffleSplit(), n_jobs=7, return_train_score=True)


In [131]:
train_size = 0.7
test_size = 1 - train_size

ROC_disp = None
F1_disp = None

noninf_messages = data[data['infection']=='NoInf']
inf_messages = data[data['infection']=='Inf']

for i in range(0, bootstrap):
    print(f'bootstrap number {i}')

    # fix imbalance
    noninf_downsample = resample(noninf_messages, replace=True, n_samples=ntarget_samples)
    boot_data = pd.concat([noninf_downsample, inf_messages])
    print(boot_data['infection'].value_counts())

    # prep input data
    ml_data = boot_data[['GCdiff', 'k3dist', 'k6dist', 'Homology']]
    ml_target = boot_data['infection']
    ml_target = ml_target.map({'NoInf' : 0, 'Inf': 1})

    # split data
    X_train, X_test, y_train, y_test = train_test_split(ml_data, ml_target, random_state=0, test_size=test_size, train_size=train_size)
    
    # grid search
    grid_search.fit(X_train, y_train)

    print("Test set score: {:.2f}".format(grid_search.score(X_test, y_test)))
    print("Best parameters: {}".format(grid_search.best_params_))
    print("Best cross-validation score: {:.2f}".format(grid_search.best_score_))
    print("Best estimator:\n{}".format(grid_search.best_estimator_))

    model_name.append('AdaBoost')
    best_score.append(grid_search.score(X_test, y_test))




bootstrap number 0
NoInf    4155
Inf      2770
Name: infection, dtype: int64
Test set score: 0.76
Best parameters: {'learning_rate': 1, 'n_estimators': 15}
Best cross-validation score: 0.77
Best estimator:
AdaBoostClassifier(learning_rate=1, n_estimators=15)
bootstrap number 1
NoInf    4155
Inf      2770
Name: infection, dtype: int64
Test set score: 0.76
Best parameters: {'learning_rate': 1, 'n_estimators': 15}
Best cross-validation score: 0.77
Best estimator:
AdaBoostClassifier(learning_rate=1, n_estimators=15)
bootstrap number 2
NoInf    4155
Inf      2770
Name: infection, dtype: int64
Test set score: 0.77
Best parameters: {'learning_rate': 1, 'n_estimators': 15}
Best cross-validation score: 0.77
Best estimator:
AdaBoostClassifier(learning_rate=1, n_estimators=15)
bootstrap number 3
NoInf    4155
Inf      2770
Name: infection, dtype: int64
Test set score: 0.76
Best parameters: {'learning_rate': 1, 'n_estimators': 15}
Best cross-validation score: 0.77
Best estimator:
AdaBoostClassifie

## Gradient boosting classifier

In [132]:
from sklearn.ensemble import GradientBoostingClassifier

In [133]:
model = GradientBoostingClassifier()
model.fit(X_train, y_train)

print("Accuracy on training set: {:.3f}".format(model.score(X_train, y_train)))
print("Accuracy on test set: {:.3f}".format(model.score(X_test, y_test)))


Accuracy on training set: 0.834
Accuracy on test set: 0.821


### Grid search

In [134]:
param_grid = {'learning_rate': [0.1, 0.25, 0.5, 0.75, 1],
              'loss': ['log_loss', 'exponential'],
              'max_depth': [5, 7, 10, 12, 15]}


In [135]:
grid_search = GridSearchCV(GradientBoostingClassifier(), param_grid, cv=ShuffleSplit(), n_jobs=7, return_train_score=True)


In [136]:
train_size = 0.7
test_size = 1 - train_size

ROC_disp = None
F1_disp = None

noninf_messages = data[data['infection']=='NoInf']
inf_messages = data[data['infection']=='Inf']

for i in range(0, bootstrap):
    print(f'bootstrap number {i}')

    # fix imbalance
    noninf_downsample = resample(noninf_messages, replace=True, n_samples=ntarget_samples)
    boot_data = pd.concat([noninf_downsample, inf_messages])
    print(boot_data['infection'].value_counts())

    # prep input data
    ml_data = boot_data[['GCdiff', 'k3dist', 'k6dist', 'Homology']]
    ml_target = boot_data['infection']
    ml_target = ml_target.map({'NoInf' : 0, 'Inf': 1})

    # split data
    X_train, X_test, y_train, y_test = train_test_split(ml_data, ml_target, random_state=0, test_size=test_size, train_size=train_size)
    
    # grid search
    grid_search.fit(X_train, y_train)

    print("Test set score: {:.2f}".format(grid_search.score(X_test, y_test)))
    print("Best parameters: {}".format(grid_search.best_params_))
    print("Best cross-validation score: {:.2f}".format(grid_search.best_score_))
    print("Best estimator:\n{}".format(grid_search.best_estimator_))

    model_name.append('GradientBoostingClassifier')
    best_score.append(grid_search.score(X_test, y_test))




bootstrap number 0
NoInf    4155
Inf      2770
Name: infection, dtype: int64
Test set score: 0.87
Best parameters: {'learning_rate': 0.5, 'loss': 'exponential', 'max_depth': 12}
Best cross-validation score: 0.88
Best estimator:
GradientBoostingClassifier(learning_rate=0.5, loss='exponential', max_depth=12)
bootstrap number 1
NoInf    4155
Inf      2770
Name: infection, dtype: int64
Test set score: 0.88
Best parameters: {'learning_rate': 0.75, 'loss': 'exponential', 'max_depth': 15}
Best cross-validation score: 0.89
Best estimator:
GradientBoostingClassifier(learning_rate=0.75, loss='exponential', max_depth=15)
bootstrap number 2
NoInf    4155
Inf      2770
Name: infection, dtype: int64
Test set score: 0.87
Best parameters: {'learning_rate': 1, 'loss': 'log_loss', 'max_depth': 15}
Best cross-validation score: 0.88
Best estimator:
GradientBoostingClassifier(learning_rate=1, max_depth=15)
bootstrap number 3
NoInf    4155
Inf      2770
Name: infection, dtype: int64
Test set score: 0.88
Bes

## Save dataframe

In [140]:
df = pd.DataFrame()

df['model'] = model_name
df['scores'] = best_score

df

model    scores
0                           SVM  0.789702
1     StochasticDescentGradient  0.704042
2     StochasticDescentGradient  0.736766
3     StochasticDescentGradient  0.731473
4     StochasticDescentGradient  0.736766
..                          ...       ...
246  GradientBoostingClassifier  0.873917
247  GradientBoostingClassifier  0.869586
248  GradientBoostingClassifier  0.881617
249  GradientBoostingClassifier  0.874880
250  GradientBoostingClassifier  0.879692

[251 rows x 2 columns]

In [141]:
df.to_csv('ml_scores.csv')